# FreeFem++ et Maillage en EF 

**Marc BUFFAT, dpt mécanique, Université Claude Bernard Lyon 1**

<a rel="license" href="http://creativecommons.org/licenses/by-nc-sa/2.0/fr/"><img alt="Licence Creative Commons" style="border-width:0;float:right;" src="cc.png" /></a><br />Mise à disposition selon les termes de la <a rel="license" href="http://creativecommons.org/licenses/by-nc-sa/2.0/fr/">Licence Creative Commons <br> Attribution - Pas d’Utilisation Commerciale - Partage dans les Mêmes Conditions 2.0 France</a>.

In [ ]:
%matplotlib inline
%autosave 300
from  numpy import *
import matplotlib.pyplot as plt
from IPython.core.display import HTML

## Génération de maillage

### Structure de données en 2D

Maillage de $ne$ triangles et $nn$ sommets

1. Table de connexion: tableau **Tbc** de nex3 entiers

2. Coordonnées des noeuds: tableau **X** de nnx2 réels

3. Frontière (noeuds): tableau **frt** de nn entiers

4. Région (éléments): tableau **reg** de ne entiers

#### table de connexion
<img src="mesh1.png"; style="width:600px"/>

#### Frontière et région
<img style=" float:center; display:inline; width:600px;" src="mesh2.png"/>   
<img style=" float:center; display:inline; width:600px;" src="mesh3.png"/>

### Génération par transformation
Transformation conforme vers un carre unité<p>
<img style=" float:center; display:inline; width:300px;" src="quacou1.png"/>   <img style=" float:center; display:inline; width:300px;" src="quacou2.png"/>

## Voronoi
Mailleur automatique<p>
<img style=" float:center; display:inline; width:400px;" src="voronoi.png"/>

## Mailleur de FreeFem++

(c) O. Pironneau et Frédéric Hecht Paris VI [http://www.freefem.org](http://www.freefem.org/)

### FreeFem++

- mailleur automatique Voronoi P1 (2D)
- solveur matriciel pour des matrices de type elts finis
- interpréteur de commande (langage de programmation)
- création d'un fichier de commande (extension .edp)
- execution: 
         FreeFem++ probleme.edp

### Syntaxe FreeFem++

- syntaxe proche du C++
- fin instruction ;
- structure : { .. };
- variables: pi=3.1456;
- résolution d'EDP 

## Mailleur Voronoi FreeFem++

In [ ]:
from freefem import mesh
G=mesh("essai.msh")
G.info()
G.plot()

## Syntaxe FreeFem++
Langage proche de C++ (instruction terminée par ; , utilisation {} )

On définit un maillage $T_h$ par la frontière $\Gamma=\partial \Omega$ du domaine donnée par des courbes paramétrées $\Gamma_i$:

$$ x = f_i(t) \mbox{ et } y = g_i(t) \mbox{ pour } t_1\le t \le t_2$$

### description de la frontiere (sens trigonométrique)

    border nom1(t=t0,t1)
      {
        x=f1(t);
        y=g1(t);
	    label=1;
      };
	border nom2(t=t0,t1)
      {
        x=f2(t);
        y=g2(t);
		label=2;
      };
      
### description des frontieres par C.L. (label)

**création et visualisation du maillage**

On spécifie le nombre de points sur chaque frontière

    mesh Th=buildmesh(nom1(n1)+nom2(n2));
    
### sauvegarde du maillage dans un fichier

    savemesh(Th,'nom_fichier.msh');

## Exemple de fichier maillage: essai.edp    
    // définition des frontières
    border aaa(t=0,1){x=t;y=0;label=2;};
    border bbb(t=0,0.5){x=1;y=t;label=2;};
    border ccc(t=0,0.5){x=1-t;y=0.5;label=2;};
    border ddd(t=0.5,1){x=0.5;y=t;label=2;};
    border eee(t=0.5,1){x=1-t;y=1;label=2;};
    border fff(t=0,1){x=0;y=1-t;label=2;};
    // generation du maillage
    mesh Th = buildmesh (aaa(6) + bbb(4) + ccc(4) +ddd(4) + 
                         eee(4) + fff(6));
    // sauvegarde
    savemesh(Th,"essai.msh");

In [ ]:
%%bash
FreeFem++ -nw essai.edp

### Exemple
Maillage d'un cercle de rayon 1 (fichier cercle.edp)

    border gamma(t=0,2*pi) 
    { x=2*cos(t); y=2*sin(t);}
    Th=buildmesh(gamma(20));
    savemesh(Th,"cercle.msh");

In [ ]:
G=mesh('cercle.msh')
G.plot()

##  Solveur EF FreeFem++

**Définition du problème**

$$ -\Delta u = f \mbox{ avec } u_\Gamma = 0 $$

### Formulation faible

Trouvez $u(x,y)$ tel que $u_\Gamma = 0$

$$ \int_\Omega{(\frac{\partial u}{\partial x}\frac{\partial v}{\partial x} + \frac{\partial u}{\partial y}\frac{\partial v}{\partial y})} = \int_\Omega{f v\, dx dy} \ \forall v$$

### Approximation avec des éléments $P^1$


    fespace Vh(Th,P1)
    Vh u,v,f=1;

    solve Lapace(u,v)= int2d(Th)(dx(u)*dx(v) + dy(u)*dy(v)) 
           - int2d(Th)(f*v) + on(Gamma,u=0); 


In [ ]:
%%bash
FreeFem++ -nw laplace.edp

### Condition aux limites sur une frontière $\Gamma_1$
* Neuman ou Fourier 

$$u_{\Gamma_{1}}+\alpha(\frac{\partial u}{\partial n})_{\Gamma_{1}}=g$$

       on(Gamma1,id(u)+a*dnu(u)=g)

* Dirichlet

$$ u_{\Gamma_2} = u_0 $$

       on(Gamma2,u=u0)

### Formulation faible : intégrale

$$\int_\Omega{() d\Omega}$$

      int2d(Th)()
      
$$ \int_\Gamma{ () d\Gamma}$$

      int(Gamma) ()

### Liste des opérateurs

      id(), dx(), dy(), laplace(), dxx(), dyy(), dyx(), dxy()
      
**ATTENTION:** 

      dxy(u)*f = dx(f*dy(u))
      laplace(u)*(x+y)=div((x+y)*grad(u))
      
### Tracé et sauvegarde de la solution

      plot(Th);
      plot(u);    

## Script Freefem

### Structure de données

La géométrie éléments finis est stockée dans un fichier texte (avec une extension .msh) avec la structure de données suivante (format FreeFEM). Ce fichier contient les informations suivantes par ligne:

1. $n_{s}\,\,\,\, n_{t}, \, nn_f $

2. $x_{1}\,\,\, y_{1}\,\,\,\,{nf}_{1}$

3. .....

4. $x_{i}\,\,\, y_{i}\,\,\,\,{nf}_{i}$
 
5. .....

6. $x_{n_{s}}\,\,\,\, y_{n_{s}}\,\,\,\,{nf}_{n_{s}}$
 
7. $tbc_{1,1}\,\,\, tbc_{1,2}\,\,\,\,\, tbc_{1,3}\,\,\,\,\, e_{1}$
 
8. ......

9. $tbc_{k,1}\,\,\, tbc_{k,2}\,\,\,\,\, tbc_{k,3}\,\,\,\,\, e_{k}$
 
10. ......

11. $tbc_{n_{t},1}\,\,\, tbc_{n_{t},2}\,\,\,\,\, tbc_{n_{t},3}\,\,\,\,\, e_{n_{t}}$
 

où $n_{s}$ est le nombre de sommets (noeuds) du maillage, $n_{t}$ le nombre d'éléments et $nn_f$ le nombre de noeuds sur la frontière. Pour chaque noeud $i$ on donne les coordonnées $(x_{i},y_{i})$ ainsi que le numéro de la frontière ou se trouve le noeud $(nf_{i})$ (0 si le noeud est interne). Pour chaque élément $k$, on a le numéro des 3 sommets $(tbc_{k,1}\,\,\, tbc_{k,2}\,\,\,\,\, tbc_{k,3})$ ainsi que le numéro de région $e_{k}$.

Le fichier a donc $1+n_{s}+n_{t}$ lignes.


### maillage à partir de script généré sous Python

In [ ]:
from freefem import meshFreefem
# SCRIPT FREEFEM++
script="""
border aaa(t=0,1){x=t;y=0;label=2;};
border bbb(t=0,0.5){x=1;y=t;label=2;};
border ccc(t=0,0.5){x=1-t;y=0.5;label=2;};
border ddd(t=0.5,1){x=0.5;y=t;label=2;};
border eee(t=0.5,1){x=1-t;y=1;label=2;};
border fff(t=0,1){x=0;y=1-t;label=2;};
mesh Th = buildmesh (aaa(6) + bbb(4) + ccc(4) +ddd(4) + eee(4) + fff(6));
savemesh(Th,\"essai1.msh\");
"""
G=meshFreefem("essai1",script)
G.plot()

In [ ]:
script="""
border aa(t=0,2*pi) { x=2*cos(t); y=2*sin(t); label=1; };
border bb(t=0,2) {
if(t<=1) { 
    x= t-0.5; 
    y= 0.17735*sqrt(t)-0.075597*t-0.212836*(t^2)+0.17363*(t^3)-0.06254*(t^4);\
} else {
    x= 2-t-0.5;
    y= -(0.17735*sqrt(2-t)-0.075597*(2-t)-0.212836*((2-t)^2)+0.17363*((2-t)^3) - 0.06254*(2-t)^4);\
}; 
label=2; }
mesh Th=buildmesh(aa(40)+bb(41));
savemesh(Th,"naca.msh");
"""
G=meshFreefem("naca",script)
plt.figure(figsize=(14,8))
G.plot(front=False)

In [ ]:
script="""
real a=2.,b=1.; 
border Gamma(t=0,2*pi)  { x = a * cos(t);   y = b*sin(t); label=1; }
border Gamma2(t=0,2*pi) { x = 0.5 * cos(t); y = 0.5*sin(-t); label=2; }
// maillage
mesh Th=buildmesh(Gamma(40)+Gamma2(80));
savemesh(Th,"ellipse2.msh");
"""
G=meshFreefem("ellipse2",script)
plt.figure(figsize=(14,8))
G.plot(front=False)

## Exemple: déformation d'une membrane

In [ ]:
from freefem import Freefem,readres
# execution script FreeFem avec lecture du resultat
script="""
real theta=4.*pi/3.;real a=2.,b=1.; func Z=0.;
border Gamma1(t=0,theta)    { x = a * cos(t); y = b*sin(t); label=1; }
border Gamma2(t=theta,2*pi) { x = a * cos(t); y = b*sin(t); label=2; }
// maillage
mesh Th=buildmesh(Gamma1(40)+Gamma2(20));
savemesh(Th,"membrane.msh");
// solveur
fespace Vh(Th,P1);
Vh phi,w, f=1;
solve Laplace(phi,w)=int2d(Th)(dx(phi)*dx(w) + dy(phi)*dy(w)) - int2d(Th)(f*w) + on(Gamma2,phi=0) + on(Gamma1,phi=Z);
// ecriture resultat
{ ofstream ff("membrane.res"); 
  ff<<phi[].n<<endl; 
  for(int i=0; i<phi[].n;i++) ff<<phi[][i]<<endl; 
}
"""

Freefem("membrane",script,True)
G=mesh("membrane.msh")
G.info()
U=readres("membrane.res")
plt.figure(figsize=(16,8))
plt.subplot(1,2,1)
G.plot(False)
plt.subplot(1,2,2)
plt.axis('equal')
G.isosurf(U,"deformation")

## FIN